## Делаю upstream'ы

In [2]:
from Bio import SeqIO, Entrez
from Bio.SeqRecord import SeqRecord

Открываю большой файл с полным геномом

In [3]:
Entrez.email = 'thetsar444@gmail.com'
handle = Entrez.efetch(db='nucleotide', rettype='gb', retmode='text', id='NC_045512')
sarscov = SeqIO.read(handle, 'genbank')
handle.close()
sarscov

SeqRecord(seq=Seq('ATTAAAGGTTTATACCTTCCCAGGTAACAAACCAACCAACTTTCGATCTCTTGT...AAA', IUPACAmbiguousDNA()), id='NC_045512.2', name='NC_045512', description='Severe acute respiratory syndrome coronavirus 2 isolate Wuhan-Hu-1, complete genome', dbxrefs=['BioProject:PRJNA485481'])

Вытаскиваю из него нужные мне features - гены вместе с координатами их начала, чтобы правильно составить таблицу

In [12]:
for feature in sarscov.features:
    if feature.type == 'CDS':
        print(feature.qualifiers['gene'][0], feature.location.start)

ORF1ab 265
ORF1ab 265
S 21562
ORF3a 25392
E 26244
M 26522
ORF6 27201
ORF7a 27393
ORF7b 27755
ORF8 27893
N 28273
ORF10 29557


Здесь же я уже составляю список с готовыми правильно вырезанными upstream'ами:

In [10]:
newseqs = []
for feature in sarscov.features:
    if feature.type == 'CDS':
        featname = feature.qualifiers['gene'][0]
        featstart = feature.location.start
        if featname == 'ORF1ab':
            newseqs.append(SeqRecord(sarscov.seq[:featstart], id=f'{featname}_upstream|[:{featstart - 1}]-from-NC_045512.2', description=''))
        else:
            newseqs.append(SeqRecord(sarscov.seq[featstart - 101:featstart], id=f'{featname}_upstream|[{featstart - 101}:{featstart - 1}]-from-NC_045512.2', description=''))
newseqs[1:]

[SeqRecord(seq=Seq('ATTAAAGGTTTATACCTTCCCAGGTAACAAACCAACCAACTTTCGATCTCTTGT...AAG', IUPACAmbiguousDNA()), id='ORF1ab_upstream|[:264]-from-NC_045512.2', name='<unknown name>', description='', dbxrefs=[]),
 SeqRecord(seq=Seq('TGATATGATTTTATCTCTTCTTAGTAAAGGTAGACTTATAATTAGAGAAAACAA...ACA', IUPACAmbiguousDNA()), id='S_upstream|[21461:21561]-from-NC_045512.2', name='<unknown name>', description='', dbxrefs=[]),
 SeqRecord(seq=Seq('CTCAAGGGCTGTTGTTCTTGTGGATCCTGCTGCAAATTTGATGAAGACGACTCT...CTT', IUPACAmbiguousDNA()), id='ORF3a_upstream|[25291:25391]-from-NC_045512.2', name='<unknown name>', description='', dbxrefs=[]),
 SeqRecord(seq=Seq('GTTCATCCGGAGTTGTTAATCCAGTAATGGAACCAATTTATGATGAACCGACGA...CTT', IUPACAmbiguousDNA()), id='E_upstream|[26143:26243]-from-NC_045512.2', name='<unknown name>', description='', dbxrefs=[]),
 SeqRecord(seq=Seq('TCTCGTGTTAAAAATCTGAATTCTTCTAGAGTTCCTGATCTTCTGGTCTAAACG...GCC', IUPACAmbiguousDNA()), id='M_upstream|[26421:26521]-from-NC_045512.2', name='<unknown name>', de

Сформировал список из наших upstream'ов, добавив им необходимое описание

Записываю полученный список в файл в формате fasta

In [11]:
SeqIO.write(newseqs[1:], 'upstreams.fasta', 'fasta')

11

## Делаю PWM из полученных сигналов

Открываю файл с выравниванием сигналов:

In [4]:
with open('align.txt') as align_file:
    lines = [line.strip() for line in align_file.readlines()]
lines

['TAAACGAAC',
 'TAAACGAAC',
 'TAAACGAAC',
 'TAAACGAAC',
 'TAAACGAAC',
 'TAAACGAAC',
 'TAAACGAAC',
 'TAATGGAAC',
 'TAAACACAG']

In [5]:
import pandas as pd
import numpy as np

Сделал из выравнивания табличку:

In [6]:
dct = {}
for index, col in enumerate(zip(*lines)):
    dct[index + 1] = col
df = pd.DataFrame(dct)
df

1  2  3  4  5  6  7  8  9
0  T  A  A  A  C  G  A  A  C
1  T  A  A  A  C  G  A  A  C
2  T  A  A  A  C  G  A  A  C
3  T  A  A  A  C  G  A  A  C
4  T  A  A  A  C  G  A  A  C
5  T  A  A  A  C  G  A  A  C
6  T  A  A  A  C  G  A  A  C
7  T  A  A  T  G  G  A  A  C
8  T  A  A  A  C  A  C  A  G

**Матрица количества нуклеотидов:**

In [7]:
df1 = pd.DataFrame(index=['A', 'T', 'C', 'G', 'sum'])
for col in df.columns:
    align_col = df[col].to_list()
    df1[col] = [align_col.count('A'), align_col.count('T'), align_col.count('C'), align_col.count('G'), len(align_col)]
df1

1  2  3  4  5  6  7  8  9
A    0  9  9  8  0  1  8  9  0
T    9  0  0  1  0  0  0  0  0
C    0  0  0  0  8  0  1  0  8
G    0  0  0  0  1  8  0  0  1
sum  9  9  9  9  9  9  9  9  9

**Матрица частот нуклеотидов с псевдоотчетами (в долях)**

In [8]:
df2 = pd.DataFrame(index=['A', 'T', 'C', 'G', 'sum'])
df2['epsilon'] = [0.001, 0.001, 0.001, 0.001, 0.004]
tmplst = []
for col in df1.columns:
    for i in df1[col].index:
        tmplst.append((df1[col][i] + df2['epsilon'][i]) / (df1[col]['sum'] + df2['epsilon']['sum']))
    df2[col] = tmplst
    tmplst = []
df2

epsilon         1         2         3         4         5         6  \
A      0.001  0.000111  0.999667  0.999667  0.888605  0.000111  0.111173   
T      0.001  0.999667  0.000111  0.000111  0.111173  0.000111  0.000111   
C      0.001  0.000111  0.000111  0.000111  0.000111  0.888605  0.000111   
G      0.001  0.000111  0.000111  0.000111  0.000111  0.111173  0.888605   
sum    0.004  1.000000  1.000000  1.000000  1.000000  1.000000  1.000000   

            7         8         9  
A    0.888605  0.999667  0.000111  
T    0.000111  0.000111  0.000111  
C    0.111173  0.000111  0.888605  
G    0.000111  0.000111  0.111173  
sum  1.000000  1.000000  1.000000

**PWM с псевдоотчетами**

In [9]:
df3 = df2.drop(columns=['epsilon'])

GC = 0.38 # GC% of SARS-CoV-2
E_col = [(1 - GC) / 2, (1 - GC) / 2, GC / 2, GC / 2, 1]

df4 = pd.DataFrame(index=['A', 'T', 'C', 'G', 'sum'])
df4['E'] = E_col

tmplst = []
for col in df3.columns:
    for i in df3[col].index:
        tmplst.append(np.log(df3[col][i] / df4['E'][i]))
    df4[col] = tmplst
    tmplst = []
df4

E         1         2         3         4         5         6  \
A    0.31 -7.934241  1.170850  1.170850  1.053081 -7.934241 -1.025486   
T    0.31  1.170850 -7.934241 -7.934241 -1.025486 -7.934241 -7.934241   
C    0.19 -7.444693 -7.444693 -7.444693 -7.444693  1.542629 -7.444693   
G    0.19 -7.444693 -7.444693 -7.444693 -7.444693 -0.535938  1.542629   
sum  1.00  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   

            7         8         9  
A    1.053081  1.170850 -7.934241  
T   -7.934241 -7.934241 -7.934241  
C   -0.535938 -7.444693  1.542629  
G   -7.444693 -7.444693 -0.535938  
sum  0.000000  0.000000  0.000000

Исправляем строчку суммы в PWM:

In [10]:
for col in df4.drop(columns='E'):
    df4.loc['sum', col] = df4.loc[['A', 'T', 'C', 'G'], col].sum()
df4 = np.round(df4, 2)
df4

E      1      2      3      4      5      6      7      8      9
A    0.31  -7.93   1.17   1.17   1.05  -7.93  -1.03   1.05   1.17  -7.93
T    0.31   1.17  -7.93  -7.93  -1.03  -7.93  -7.93  -7.93  -7.93  -7.93
C    0.19  -7.44  -7.44  -7.44  -7.44   1.54  -7.44  -0.54  -7.44   1.54
G    0.19  -7.44  -7.44  -7.44  -7.44  -0.54   1.54  -7.44  -7.44  -0.54
sum  1.00 -21.65 -21.65 -21.65 -14.86 -14.86 -14.86 -14.86 -21.65 -14.86

Записываю полученную правильную матрицу в html-таблицу, чтобы вставить её в отчёт:

In [11]:
df4.to_html('table.html')